*Created by: Daryl James Padogdog*

# **Gold Price Prediction Using Dual-Timeframe LSTM (Big Brother / Little Brother Model)**

📌 Overview

This notebook implements a **dual-timeframe LSTM-based price prediction system for Gold (XAUUSD)** using historical market data.
The system mimics how human traders analyze the market by combining:


*  **Higher timeframe trend analysis (1H candles)**
*   **Lower timeframe entry confirmation (5-minute candles)**


To achieve this, two separate LSTM models are trained:


*   **Big Brother Model →** Identifies the overall market trend
*   **Little Brother Model →** Confirms precise trade entries



The final output is a BUY / SELL / WAIT trading signal based on the alignment of both models.



**🧠 Concept: Big Brother vs Little Brother**
**Model** Big Brother

**Timeframe**	 1 Hour

**Purpose** Determines overall market trend (Bullish / Bearish)


**Model** Little Brother

**Timeframe**	5 Minutes

**Purpose**  Confirms short-term entry or exit signals

**The system only enters trades when both timeframes agree, reducing false signals and improving decision reliability.**

In [1]:
import numpy as np
import pandas as pd
from sklearn.preprocessing import MinMaxScaler
from tensorflow.keras.models import Sequential, load_model
from tensorflow.keras.layers import LSTM, Dense, Dropout
from tensorflow.keras.callbacks import EarlyStopping

In [2]:
# ==========================================
# 1. CONFIGURATION
# ==========================================
# Files
FILE_BIG = 'XAU_1h_data.csv'
FILE_SMALL = 'XAU_5m_data.csv'

# Lookbacks
LOOKBACK_BIG = 720
LOOKBACK_SMALL = 48

# Model Names
MODEL_BIG_NAME = 'big_brother_model.keras'
MODEL_SMALL_NAME = 'little_brother_model.keras'

In [3]:
# ==========================================
# 2. HELPER FUNCTIONS
# ==========================================
# Load Data
def create_dataset(dataset, look_back=60):
    x, y = [], []
    for i in range(look_back, len(dataset)):
        x.append(dataset[i-look_back:i, 0])
        y.append(dataset[i, 0])
    x, y = np.array(x), np.array(y)
    x = np.reshape(x, (x.shape[0], x.shape[1], 1))
    return x, y

def train_model(x_train, y_train, model_name):
    """Builds and trains an LSTM model with Early Stopping"""
    model = Sequential()
    # Layer 1
    model.add(LSTM(100, return_sequences=True, input_shape=(x_train.shape[1], 1)))
    model.add(Dropout(0.2))
    # Layer 2
    model.add(LSTM(100, return_sequences=False))
    model.add(Dropout(0.2))
    # Output
    model.add(Dense(25))
    model.add(Dense(1))

    model.compile(optimizer='adam', loss='mean_squared_error')

    stopper = EarlyStopping(monitor='val_loss', patience=5, restore_best_weights=True)

    print(f"Training {model_name}...")
    model.fit(x_train, y_train, batch_size=64, epochs=100,
              validation_split=0.1, callbacks=[stopper], verbose=1)

    model.save(model_name)
    print(f"Saved {model_name}")
    return model

In [4]:
# ==========================================
# 3. LOAD & PREPROCESS DATA
# ==========================================
print("Loading Data...")

df_big = pd.read_csv(FILE_BIG, sep=';')
df_big['Date'] = pd.to_datetime(df_big['Date'], format='%Y.%m.%d %H:%M')
df_big = df_big.sort_values('Date')
data_big = df_big.filter(['Close']).values

scaler_big = MinMaxScaler(feature_range=(0, 1))
scaled_big = scaler_big.fit_transform(data_big)

df_small = pd.read_csv(FILE_SMALL, sep=';')
df_small['Date'] = pd.to_datetime(df_small['Date'])
df_small = df_small.sort_values('Date')
data_small = df_small.filter(['Close']).values

scaler_small = MinMaxScaler(feature_range=(0, 1))
scaled_small = scaler_small.fit_transform(data_small)

Loading Data...


In [5]:
# ==========================================
# 4. TRAINING PHASE
# ==========================================

train_len_big = int(len(scaled_big) * 0.9)
x_train_big, y_train_big = create_dataset(scaled_big[:train_len_big], LOOKBACK_BIG)

train_len_small = int(len(scaled_small) * 0.9)
x_train_small, y_train_small = create_dataset(scaled_small[:train_len_small], LOOKBACK_SMALL)

# Train Both Models
big_model = train_model(x_train_big, y_train_big, MODEL_BIG_NAME)
small_model = train_model(x_train_small, y_train_small, MODEL_SMALL_NAME)

/usr/local/lib/python3.12/dist-packages/keras/src/layers/rnn/rnn.py:199: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


Training big_brother_model.keras...
Epoch 1/100
1555/1555 ━━━━━━━━━━━━━━━━━━━━ 90s 55ms/step - loss: 6.6738e-04 - val_loss: 4.7518e-06
Epoch 2/100
1555/1555 ━━━━━━━━━━━━━━━━━━━━ 86s 55ms/step - loss: 4.2776e-05 - val_loss: 4.0521e-06
Epoch 3/100
1555/1555 ━━━━━━━━━━━━━━━━━━━━ 85s 55ms/step - loss: 4.3991e-05 - val_loss: 8.0972e-06
Epoch 4/100
1555/1555 ━━━━━━━━━━━━━━━━━━━━ 91s 58ms/step - loss: 4.6191e-05 - val_loss: 5.3233e-05
Epoch 5/100
1555/1555 ━━━━━━━━━━━━━━━━━━━━ 85s 54ms/step - loss: 4.5528e-05 - val_loss: 7.4747e-06
Epoch 6/100
1555/1555 ━━━━━━━━━━━━━━━━━━━━ 92s 59ms/step - loss: 4.4293e-05 - val_loss: 5.5608e-06
Epoch 7/100
1555/1555 ━━━━━━━━━━━━━━━━━━━━ 86s 55ms/step - loss: 4.3839e-05 - val_loss: 3.0839e-06
Epoch 8/100
1555/1555 ━━━━━━━━━━━━━━━━━━━━ 86s 55ms/step - loss: 4.1929e-05 - val_loss: 6.6302e-06
Epoch 9/100
1555/1555 ━━━━━━━━━━━━━━━━━━━━ 84s 54ms/step - loss: 4.2167e-05 - val_loss: 5.2890e-06
Epoch 10/100
1555/1555 ━━━━━━━━━━━━━━━━━━━━ 143s 55ms/step - loss: 4.1319

In [6]:
# ==========================================
# 5. LIVE TRADING SIMULATION
# ==========================================
print("\n===========================================")
print("     AI TRADING SYSTEM ANALYSIS")
print("===========================================")

# 1. Get the very latest data
last_big_seq = scaled_big[-LOOKBACK_BIG:]
last_small_seq = scaled_small[-LOOKBACK_SMALL:]

# 2. Reshape for Prediction
input_big = np.reshape(last_big_seq, (1, LOOKBACK_BIG, 1))
input_small = np.reshape(last_small_seq, (1, LOOKBACK_SMALL, 1))

# 3. Predict
pred_big_scaled = big_model.predict(input_big, verbose=0)
pred_small_scaled = small_model.predict(input_small, verbose=0)

# 4. Convert to Prices
target_big = scaler_big.inverse_transform(pred_big_scaled)[0][0]
target_small = scaler_small.inverse_transform(pred_small_scaled)[0][0]

current_price_big = data_big[-1][0]
current_price_small = data_small[-1][0]


     AI TRADING SYSTEM ANALYSIS


In [7]:
# ==========================================
# 6. DECISION LOGIC
# ==========================================

print(f"Current Market Price (5m): ${current_price_small:.2f}")



#=================================
# --- Big Brother Analysis ---
#=================================
trend = "NEUTRAL"
if target_big > current_price_big:
    trend = "UP"
    print(f"[Big Brother] 1H Trend: BULLISH (Target: ${target_big:.2f})")
else:
    trend = "DOWN"
    print(f"[Big Brother] 1H Trend: BEARISH (Target: ${target_big:.2f})")




#=================================
# --- Little Brother Analysis ---
#=================================
signal = "WAIT"

if trend == "UP":
    if target_small > current_price_small:
        signal = "BUY NOW"
        print(f"[Little Brother] 5m Entry: CONFIRMED (Target: ${target_small:.2f})")
    else:
        signal = "WAIT TO BUY"
        print(f"[Little Brother] 5m Entry: WAIT (Price dipping to ${target_small:.2f})")
        print("   -> Wait for the dip to finish, then buy.")

elif trend == "DOWN":
    if target_small < current_price_small:
        signal = "SELL NOW"
        print(f"[Little Brother] 5m Entry: CONFIRMED (Target: ${target_small:.2f})")
    else:
        signal = "WAIT TO SELL"
        print(f"[Little Brother] 5m Entry: WAIT (Price rallying to ${target_small:.2f})")
        print("   -> Wait for the rally to finish, then sell.")

print("\n-------------------------------------------")
print(f"FINAL SIGNAL: {signal}")
print("-------------------------------------------")

Current Market Price (5m): $4246.13
[Big Brother] 1H Trend: BEARISH (Target: $3956.73)
[Little Brother] 5m Entry: WAIT (Price rallying to $4252.01)
   -> Wait for the rally to finish, then sell.

-------------------------------------------
FINAL SIGNAL: WAIT TO SELL
-------------------------------------------


In [22]:
#========================================
# --- test data throughout the year --- #
#========================================

import numpy as np
import pandas as pd
import plotly.graph_objects as go
from sklearn.preprocessing import MinMaxScaler
from tensorflow.keras.models import load_model

FILE_BIG = 'XAU_1h_data.csv'
FILE_SMALL = 'XAU_5m_data.csv'
LOOKBACK_BIG = 720
LOOKBACK_SMALL = 48
TEST_PERIOD_DAYS = 365

print("Loading Data (365 days)...")

df_big = pd.read_csv(FILE_BIG, sep=';')
df_big['Date'] = pd.to_datetime(df_big['Date'], format='%Y.%m.%d %H:%M')
df_big = df_big.sort_values('Date')
data_big = df_big['Close'].values.reshape(-1, 1)

df_small = pd.read_csv(FILE_SMALL, sep=';')
df_small['Date'] = pd.to_datetime(df_small['Date'])
df_small = df_small.sort_values('Date')
data_small = df_small['Close'].values.reshape(-1, 1)

scaler_small = MinMaxScaler(feature_range=(0, 1))
scaled_small = scaler_small.fit_transform(data_small)

steps_to_test = TEST_PERIOD_DAYS * 24 * 12
start_index = len(data_small) - steps_to_test
if start_index < LOOKBACK_SMALL: start_index = LOOKBACK_SMALL

test_data_real = data_small[start_index:]
test_dates = df_small['Date'].values[start_index:]

print(f"Analyzing {steps_to_test} candles... This may take 1-2 minutes.")

model_small = load_model('little_brother_model.keras')

X_test_small = []
for i in range(start_index, len(data_small)):
    X_test_small.append(scaled_small[i-LOOKBACK_SMALL:i, 0])

X_test_small = np.array(X_test_small)
X_test_small = np.reshape(X_test_small, (X_test_small.shape[0], X_test_small.shape[1], 1))

predicted_scaled = model_small.predict(X_test_small, verbose=1)
predicted_prices = scaler_small.inverse_transform(predicted_scaled)


wins = 0
total_trades = 0

for i in range(len(test_data_real) - 1):
    current_price = test_data_real[i][0]
    predicted_next = predicted_prices[i][0]
    actual_next = test_data_real[i+1][0]

    # AI Signal
    if predicted_next > current_price:
        signal = "BUY"
    else:
        signal = "SELL"

    # Check Result
    if signal == "BUY" and actual_next > current_price:
        wins += 1
    elif signal == "SELL" and actual_next < current_price:
        wins += 1

    total_trades += 1

# --- New Calculations ---
losses = total_trades - wins
win_rate = (wins / total_trades) * 100

print(f"--------------------------------")
print(f"WIN RATE (Last 365 Days): {win_rate:.2f}%")
print(f"Total Candles: {total_trades}")
print(f"Total Wins: {wins}")      # Added
print(f"Total Losses: {losses}")  # Added
print(f"--------------------------------")

fig = go.Figure()

fig.add_trace(go.Scatter(
    x=test_dates,
    y=test_data_real.flatten(),
    mode='lines',
    name='Real Price',
    line=dict(color='#00FF00', width=1)
))

fig.add_trace(go.Scatter(
    x=test_dates,
    y=predicted_prices.flatten(),
    mode='lines',
    name='AI Prediction',
    line=dict(color='#FFFF00', width=1, dash='dot')
))

fig.update_layout(
    title=f'AI Performance (Last 365 Days) - Win Rate: {win_rate:.2f}%',
    xaxis_title='Date',
    yaxis_title='Price (USD)',
    template='plotly_dark',
    xaxis_rangeslider_visible=False,
    height=700
)

fig.show()

Loading Data (365 days)...
Analyzing 105120 candles... This may take 1-2 minutes.
3285/3285 ━━━━━━━━━━━━━━━━━━━━ 10s 3ms/step
--------------------------------
WIN RATE (Last 365 Days): 50.78%
Total Candles: 105119
Total Wins: 53384
Total Losses: 51735
--------------------------------
